In [1]:
'''!pip install matplotlib
!pip install seaborn
!pip install plotly.express

!pip install numpy
!pip install pandas
!pip install nbformat
!pip install sklearn
!pip install scikit-learn'''

'!pip install matplotlib\n!pip install seaborn\n!pip install plotly.express\n\n!pip install numpy\n!pip install pandas\n!pip install nbformat\n!pip install sklearn\n!pip install scikit-learn'

In [50]:
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

import numpy as np
import pandas as pd

from sklearn.metrics import confusion_matrix, accuracy_score, recall_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression, SGDClassifier
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

from scipy import stats

In [3]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [4]:
def inspect_values(df: pd.DataFrame) -> None:
    '''
    extensive overview of data
    '''
    for column in df.columns:
        print(f"column: {column}", end=' - ')
        if (df[column].dtype not in ['float64', 'int64', 'datetime64[ns]']) or (df[column].nunique() < 15):
            print(f"unique values: {df[column].unique()}", end=' - ')
        else:
            print(f"values: from {min(df[column])} to {max(df[column])}", end=' - ')
        print(f"datatype: {df[column].dtype}" , end=' - ')
        print('number of NaN values:', df[column].isna().sum())

In [5]:
clients = pd.read_csv('data/train/client_train.csv', low_memory=False, parse_dates=True)
invoices = pd.read_csv('data/train/invoice_train.csv', low_memory=False, parse_dates=True)

In [6]:
inspect_values(clients)

column: disrict - unique values: [60 69 62 63] - datatype: int64 - number of NaN values: 0
column: client_id - unique values: ['train_Client_0' 'train_Client_1' 'train_Client_10' ...
 'train_Client_99997' 'train_Client_99998' 'train_Client_99999'] - datatype: object - number of NaN values: 0
column: client_catg - unique values: [11 12 51] - datatype: int64 - number of NaN values: 0
column: region - values: from 101 to 399 - datatype: int64 - number of NaN values: 0
column: creation_date - unique values: ['31/12/1994' '29/05/2002' '13/03/1986' ... '16/08/2004' '30/08/1978'
 '25/05/1978'] - datatype: object - number of NaN values: 0
column: target - unique values: [0. 1.] - datatype: float64 - number of NaN values: 0


In [20]:
inspect_values(invoices)

column: client_id - unique values: ['train_Client_0' 'train_Client_1' 'train_Client_10' ...
 'train_Client_99997' 'train_Client_99998' 'train_Client_99999'] - datatype: object - number of NaN values: 0
column: invoice_date - unique values: ['2014-03-24' '2013-03-29' '2015-03-23' ... '1995-11-28' '1982-07-04'
 '1996-09-02'] - datatype: object - number of NaN values: 0
column: tarif_type - values: from 8 to 45 - datatype: int64 - number of NaN values: 0
column: counter_number - values: from 0 to 27981145458733 - datatype: int64 - number of NaN values: 0
column: counter_statue - unique values: ['0' '1' '5' '4' '3' '2' '769' 'A' '618' '269375' '46' '420'] - datatype: object - number of NaN values: 0
column: counter_code - values: from 0 to 600 - datatype: int64 - number of NaN values: 0
column: reading_remarque - unique values: [  8   6   9   7 207 413 203   5] - datatype: int64 - number of NaN values: 0
column: counter_coefficient - values: from 0 to 50 - datatype: int64 - number of NaN v

In [7]:
# px.histogram(invoices[invoices['months_number'] < 12], x='months_number', histfunc='count')

In [8]:
invoices['total_consommation'] = invoices.eval("consommation_level_1 + consommation_level_2 + consommation_level_3 + consommation_level_4")

In [9]:
invoices_grouped = invoices.groupby('client_id').mean(numeric_only=True)
invoices_grouped.rename(mapper={'total_consommation': 'mean_total_consommation'}, axis=1, inplace=True)
invoices_grouped = invoices_grouped.reset_index()
invoices_grouped.head(10)


client_id  tarif_type  counter_number  counter_code  \
0       train_Client_0   11.000000    1.335667e+06    203.685714   
1       train_Client_1   11.000000    6.789020e+05    203.000000   
2      train_Client_10   11.000000    5.727650e+05    203.222222   
3     train_Client_100   11.000000    2.078000e+03    413.000000   
4    train_Client_1000   11.000000    1.957500e+04    207.000000   
5   train_Client_10000   22.479167    8.149729e+05    124.625000   
6  train_Client_100000   25.500000    4.446350e+04    209.000000   
7  train_Client_100001   25.128205    5.904181e+05    106.538462   
8  train_Client_100002   11.000000    1.441290e+05    413.000000   
9  train_Client_100003   11.000000    5.868000e+05    467.000000   

   reading_remarque  counter_coefficient  consommation_level_1  \
0          6.971429                  1.0            352.400000   
1          7.216216                  1.0            557.540541   
2          7.055556                  1.0            798.611111   
3          6.150000                  1.0              1.200000   
4          8.857143                  1.0            663.714286   
5          7.708333                  1.0            352.104167   
6          7.975000                  1.0            280.025000   
7          7.025641                  1.0            327.500000   
8          7.500000                  1.0            112.500000   
9          9.000000                  1.0            850.800000   

   consommation_level_2  consommation_level_3  consommation_level_4  \
0             10.571429              0.000000              0.000000   
1              0.000000              0.000000              0.000000   
2             37.888889              0.000000              0.000000   
3              0.000000              0.000000              0.000000   
4            104.857143            117.357143             36.714286   
5             10.437500              3.770833              0.000000   
6              6.550000              0.000000              0.000000   
7              0.923077              0.000000              0.000000   
8              0.000000              0.000000              0.000000   
9           1629.200000            320.000000           4882.000000   

      old_index     new_index  months_number  mean_total_consommation  
0   9444.542857   9807.514286       4.628571               362.971429  
1  14330.756757  14888.297297       4.324324               557.540541  
2  32873.000000  33709.500000       6.444444               836.500000  
3     94.150000     95.350000       4.200000                 1.200000  
4   6900.428571   7823.071429       3.714286               922.642857  
5  13789.625000  14155.937500       4.000000               366.312500  
6  19788.750000  20075.325000       3.700000               286.575000  
7   6583.141026   6911.564103       3.871795               328.423077  
8      3.500000    116.000000       4.000000               112.500000  
9   9342.200000  17024.200000       4.000000              7682.000000

In [12]:
agg_clients = pd.merge(left=clients, right=invoices_grouped[['client_id', 'mean_total_consommation']], how='left')

In [18]:
count_num = invoices.groupby('client_id').counter_number.nunique().to_frame('number_of_counter_numbers').reset_index()

agg_clients = pd.merge(left=agg_clients, right=count_num, on='client_id')

In [60]:
counter_dict = {'A': 0, '0': 0, '1': 1, '5': 5, '4': 4, '3': 3, '2': 2, '769': 0, '618': 0, '269375': 0, '46': 0, '420': 0}
invoices.counter_statue = invoices.counter_statue.map(lambda x: counter_dict.get(x, x))

invoices.counter_statue.unique()

array([0, 1, 5, 4, 3, 2])

In [75]:
df = pd.merge(left=clients, right=invoices, on='client_id', how='left')

counter_statues = df.groupby('client_id').counter_statue.apply(stats.mode).apply(lambda x: x[0]).to_frame('mode_counter_statue').reset_index()
agg_clients = pd.merge(left=agg_clients, right=counter_statues, on='client_id')

In [78]:
df.groupby(['reading_remarque', 'target']).size()

reading_remarque  target
5                 0.0             1
6                 0.0       2059001
                  1.0        171938
7                 0.0           660
                  1.0             1
8                 0.0        760354
                  1.0         67769
9                 0.0       1303588
                  1.0        113404
203               0.0            15
207               0.0             6
413               0.0            12
dtype: int64

In [80]:
remarque_dict = {5: 6, 207: 6, 413: 6, 203: 6}
invoices.reading_remarque = invoices.reading_remarque.map(lambda x: remarque_dict.get(x, x))

invoices.reading_remarque.unique()

array([8, 6, 9, 7])

In [81]:
reading_mode = invoices.groupby('client_id').reading_remarque.apply(stats.mode).apply(lambda x: x[0]).to_frame('mode_reading_remarque').reset_index()
agg_clients = pd.merge(left=agg_clients, right=reading_mode, on='client_id')

In [37]:
min_max = invoices.groupby('client_id').total_consommation.aggregate(['min', 'max'])
rng_total_consommation = min_max.apply(lambda x: x.to_list()[1] - x.to_list()[0], axis=1).to_frame('range_total_consommation').reset_index()

agg_clients = pd.merge(left=agg_clients, right=rng_total_consommation, on='client_id')

In [14]:
std_consommation = invoices.groupby('client_id').total_consommation.std().reset_index()
std_consommation.rename(mapper={'total_consommation': 'std_total_consommation'}, axis=1, inplace=True)
agg_clients = pd.merge(left=agg_clients, right=std_consommation, on='client_id')


disrict            client_id  client_catg  region creation_date  target  \
0       60       train_Client_0           11     101    31/12/1994     0.0   
1       69       train_Client_1           11     107    29/05/2002     0.0   
2       62      train_Client_10           11     301    13/03/1986     0.0   
3       69     train_Client_100           11     105    11/07/1996     0.0   
4       62    train_Client_1000           11     303    14/10/2014     0.0   
5       69   train_Client_10000           11     103    29/09/1993     0.0   
6       62  train_Client_100000           11     309    07/06/2012     0.0   
7       60  train_Client_100001           11     101    12/04/2006     0.0   
8       62  train_Client_100002           11     301    31/12/2006     0.0   
9       60  train_Client_100003           11     101    25/10/2011     0.0   

   mean_total_consommation  counter_number  std_total_consommation  
0               362.971429               1              341.553930  
1               557.540541               1              197.935960  
2               836.500000               1              646.808386  
3                 1.200000               1                3.607011  
4               922.642857               1              633.485669  
5               366.312500               2              383.955237  
6               286.575000               2              338.205437  
7               328.423077               2              295.575622  
8               112.500000               1              149.199531  
9              7682.000000               1             6750.877980

In [ ]:
# TODO: has both elec and gaz

In [76]:
agg_clients.head(10)

disrict            client_id  client_catg  region creation_date  target  \
0       60       train_Client_0           11     101    31/12/1994     0.0   
1       69       train_Client_1           11     107    29/05/2002     0.0   
2       62      train_Client_10           11     301    13/03/1986     0.0   
3       69     train_Client_100           11     105    11/07/1996     0.0   
4       62    train_Client_1000           11     303    14/10/2014     0.0   
5       69   train_Client_10000           11     103    29/09/1993     0.0   
6       62  train_Client_100000           11     309    07/06/2012     0.0   
7       60  train_Client_100001           11     101    12/04/2006     0.0   
8       62  train_Client_100002           11     301    31/12/2006     0.0   
9       60  train_Client_100003           11     101    25/10/2011     0.0   

   mean_total_consommation  counter_number  std_total_consommation  \
0               362.971429               1              341.553930   
1               557.540541               1              197.935960   
2               836.500000               1              646.808386   
3                 1.200000               1                3.607011   
4               922.642857               1              633.485669   
5               366.312500               2              383.955237   
6               286.575000               2              338.205437   
7               328.423077               2              295.575622   
8               112.500000               1              149.199531   
9              7682.000000               1             6750.877980   

   number_of_counter_numbers  range_total_consommation  mode_counter_statue  
0                          1                      1348                    0  
1                          1                      1017                    0  
2                          1                      2894                    0  
3                          1                        15                    0  
4                          1                      2258                    0  
5                          2                      1414                    0  
6                          2                      1462                    0  
7                          2                      1101                    0  
8                          1                       211                    0  
9                          1                     17003                    0

In [83]:
X = agg_clients.drop(['target', 'client_id', 'creation_date'], axis=1)
y = agg_clients.target

X_train, X_test, y_train , y_test = train_test_split(X, y, random_state=0)

In [99]:
log_reg = KNeighborsClassifier(n_neighbors=9)
log_reg.fit(X_train, y_train)
y_train_pred = log_reg.predict(X_train)
y_test_pred = log_reg.predict(X_test)

confusion_matrix(y_test, y_test_pred)

array([[38336,    21],
       [ 2287,     4]])

In [91]:
X.std_total_consommation = X.std_total_consommation.fillna(0)

In [92]:
inspect_values(X)

column: disrict - unique values: [60 69 62 63] - datatype: int64 - number of NaN values: 0
column: client_catg - unique values: [11 12 51] - datatype: int64 - number of NaN values: 0
column: region - values: from 101 to 399 - datatype: int64 - number of NaN values: 0
column: mean_total_consommation - values: from 0.0 to 117483.0 - datatype: float64 - number of NaN values: 0
column: counter_number - unique values: [1 2 3 4 5 8 6 7] - datatype: int64 - number of NaN values: 0
column: std_total_consommation - values: from 0.0 to 163788.26784551246 - datatype: float64 - number of NaN values: 0
column: number_of_counter_numbers - unique values: [1 2 3 4 5 8 6 7] - datatype: int64 - number of NaN values: 0
column: range_total_consommation - values: from 0 to 999809 - datatype: int64 - number of NaN values: 0
column: mode_counter_statue - unique values: [0 1 5 4 3 2] - datatype: int64 - number of NaN values: 0
column: mode_reading_remarque - unique values: [6 9 8 7] - datatype: int64 - number

In [100]:
'''models = {
    KNeighborsClassifier: {
        "n_neighbors" : list(range(1, 31)),
        "weights" : ["uniform", "distance"],
        "p" : [1, 2, 3],
        "algorithm": ["ball_tree", "kd_tree", "brute"]},
    LogisticRegression: {
        "tol": [10**i for i in range(1, -7, -1)],
        "C": [10**i for i in range(-4, 8, 1)],
        "max_iter": [1000, 10000, 100000],
        "l1_ratio": [i/10 for i in range(1, 9, 1)],
        "penalty": ['l1', 'l2', 'elasticnet'],
        "solver": ['lbfgs', 'liblinear', 'newton-cg', 'newton-cholesky', 'sag', 'saga']},
    SGDClassifier: {
        "tol": [10**i for i in range(1, -7, -1)],
        "max_iter": [1000, 10000, 100000]},
    DecisionTreeClassifier: {
        "criterion": ['gini', 'entropy', 'log_loss'],
        "spliter": ['best', 'random'],
        "max_depth": list(range(2, 7)),
        "min_samples_leaf": [1, 5, 10, 20],
        "max_leaf_nodes": [7, 12, 18]
    }
    }'''

models = {
    KNeighborsClassifier: {
        "n_neighbors" : list(range(1, 31)),
        "weights" : ["uniform", "distance"],
        "p" : [1, 2, 3],
        "algorithm": ["ball_tree", "kd_tree", "brute"]},
    DecisionTreeClassifier: {
        "criterion": ['gini', 'entropy', 'log_loss'],
        "splitter": ['best', 'random'],
        "max_depth": list(range(2, 12)),
        "min_samples_leaf": list(range(1, 25, 2)),
        "max_leaf_nodes": list((range(4, 25, 3)))},
    RandomForestClassifier: {
        "n_estimators": [10, 50, 100],
        "criterion": ['gini', 'entropy', 'log_loss'],
        "max_depth": list(range(2, 7)),
        "min_samples_leaf": list(range(1, 25, 2)),
        "max_leaf_nodes": list((range(4, 22, 3)))}
    }

scalers = [MinMaxScaler, StandardScaler, '']

results = {}
confusions = {}
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=0)

for scaler_ in scalers:
    if scaler_:
        scaler = scaler_()
        X_train_scaled = scaler.fit_transform(X_train)
        X_test_scaled = scaler.transform(X_test)

    for model, params in models.items():
        # gs = GridSearchCV(estimator=model(), param_grid=params, scoring=['f1', 'accuracy', 'recall'], refit='f1', cv=5, verbose=1, n_jobs=-1)
        gs = RandomizedSearchCV(estimator=model(), param_distributions=params, scoring='f1', n_iter=10, cv=2, verbose=0, n_jobs=-1)
        gs.fit(X_train_scaled, y_train)
        tn, fp, fn, tp = confusion_matrix(y_test, gs.predict(X_test_scaled)).ravel()
        results[f"{str(gs.best_estimator_).split('(')[0]} - {scaler_}"] = {'params': f'{gs.best_params_}', 'refit': f'{gs.best_score_}', 'f1_test': f"{tp/(tp + (fp+fn)/2)}", 'tn': f'{tn}', 'fp': f'{fp}', 'fn': f'{fn}', 'tp': f'{tp}'}

for key, value in results.items():
    print(key, ' - ', value)

KNeighborsClassifier - <class 'sklearn.preprocessing._data.MinMaxScaler'>  -  {'params': "{'weights': 'distance', 'p': 1, 'n_neighbors': 2, 'algorithm': 'ball_tree'}", 'refit': '0.14108064328430833', 'f1_test': '0.15222173339199296', 'tn': '36448', 'fp': '1909', 'fn': '1945', 'tp': '346'}
DecisionTreeClassifier - <class 'sklearn.preprocessing._data.MinMaxScaler'>  -  {'params': "{'splitter': 'best', 'min_samples_leaf': 3, 'max_leaf_nodes': 22, 'max_depth': 11, 'criterion': 'log_loss'}", 'refit': '0.0', 'f1_test': '0.0', 'tn': '38357', 'fp': '0', 'fn': '2291', 'tp': '0'}
RandomForestClassifier - <class 'sklearn.preprocessing._data.MinMaxScaler'>  -  {'params': "{'n_estimators': 100, 'min_samples_leaf': 11, 'max_leaf_nodes': 4, 'max_depth': 2, 'criterion': 'log_loss'}", 'refit': '0.0', 'f1_test': '0.0', 'tn': '38357', 'fp': '0', 'fn': '2291', 'tp': '0'}
KNeighborsClassifier - <class 'sklearn.preprocessing._data.StandardScaler'>  -  {'params': "{'weights': 'distance', 'p': 3, 'n_neighbors

In [ ]:
invoices.groupby('client_id').months_number.nunique().sort_values(ascending=False)

client_id
train_Client_14780     184
train_Client_126995    129
train_Client_101645    127
train_Client_27546      86
train_Client_76644      86
train_Client_120317     76
train_Client_16033      69
train_Client_99465      66
train_Client_21000      54
train_Client_131075     46
train_Client_75146      43
train_Client_27303      37
train_Client_38857      36
train_Client_46249      35
train_Client_116912     31
train_Client_7894       22
train_Client_116032     19
train_Client_109609     17
train_Client_111476     16
train_Client_131550     16
train_Client_78338      15
train_Client_583        15
train_Client_22883      15
train_Client_64519      14
train_Client_39877      13
train_Client_38765      12
train_Client_36866      11
train_Client_115184     10
train_Client_52765      10
train_Client_51136      10
train_Client_99917      10
train_Client_100144      9
train_Client_99289       9
train_Client_100551      9
train_Client_23600       9
train_Client_130258      9
train_Client_11006

In [ ]:
count_num = invoices.groupby('client_id').counter_number.nunique().sort_values(ascending=False).reset_index()

merged = pd.merge(left=count_num, right=clients, on='client_id')
merged.corr(numeric_only=True)

counter_number   disrict  client_catg    region    target
counter_number        1.000000  0.081748     0.006052 -0.025975  0.193302
disrict               0.081748  1.000000     0.032836 -0.313309  0.050749
client_catg           0.006052  0.032836     1.000000 -0.041427  0.054745
region               -0.025975 -0.313309    -0.041427  1.000000  0.010940
target                0.193302  0.050749     0.054745  0.010940  1.000000

In [ ]:
# px.imshow(clients.corr(numeric_only=True), text_auto=True)

In [ ]:
# px.imshow(invoices.corr(numeric_only=True), text_auto=True, height=800, width=800)

In [ ]:
# df = pd.merge(left=invoices, right=clients, on='client_id', how='left')

In [ ]:
# df['counter_type_int'] = df.counter_type.map({'GAZ': 0, 'ELEC': 1})

In [ ]:
# df.sample()

In [ ]:
# px.imshow(df.corr(numeric_only=True), text_auto=True, width=1000, height=1000, color_continuous_scale='RdBu')

In [ ]:
# grouped = df.groupby(['target', 'client_id']).consommation_level_1.std().reset_index().groupby('target').consommation_level_1.mean()

# px.imshow(grouped.corr(numeric_only=True), text_auto=True, width=1000, height=1000)
# grouped


In [ ]:
# df['date'] = pd.to_datetime(df.invoice_date)